# Bilanciamento del dataset

In [2]:
import json
import shutil
import os


# Open the JSON file
with open(f'data/train.parameter.json') as file:
    data = json.load(file)
new_data = data.copy()
for i in data:
  if data[i]['steg_algorithm'] != 'uerd':
    new_data.pop(i)
# Access the JSON data
uerd_list = new_data.keys()

if not os.path.exists('data/uerd/cover/'):
    os.makedirs('data/uerd/cover/')
if not os.path.exists('data/uerd/stego/'):
    os.makedirs('data/uerd/stego/')


print(f"Total images: {len(data)}   Only uerd images: {len(new_data)}")
for image in uerd_list:
    for type in ['cover', 'stego']:  
      source_path = f'data/{type}/{image}'
      destination_path = f'data/uerd/{type}/{image}'
      if os.path.exists(source_path):
        shutil.move(source_path, destination_path)
        
common_images = set(os.listdir(f'data/uerd/stego/')).intersection(set(os.listdir(f'data/uerd/cover/')))

len(common_images)

Total images: 100000   Only uerd images: 33416


24428

In [3]:

for type in ['cover', 'stego']:
    source_path = f'data/uerd/{type}/'
    
    if not os.path.exists(source_path):
        os.makedirs(source_path)
    
    destination_path = f'data/uerd/removed/{type}/'
    
    if not os.path.exists(destination_path):
        os.makedirs(destination_path)
        
    to_remove = set(os.listdir(source_path)) - common_images
    
    for image in list(to_remove):
        shutil.move(source_path + image, destination_path + image)

# Data augmentation

Qui divido ogni immagine 1024x1024 in immagini da 128x128 attuando un cropping. Questo lo faccio per non sovraccaricare la memoria ram durante la fase di training del CNN.

In [4]:
import cv2

def crop_images(image_path, image_name, save_path, crop_size):
    # Carica l'immagine
    image = cv2.imread(image_path + image_name, cv2.IMREAD_COLOR)

    # Ottenere le dimensioni dell'immagine originale
    height, width, _ = image.shape

    # Assicurarsi che la cartella di output esista
    os.makedirs(save_path, exist_ok=True)

    # Calcolare il numero di tagli lungo l'asse x e y
    num_crops_x = width // crop_size
    num_crops_y = height // crop_size

    # Effettua il taglio dell'immagine in immagini più piccole e salva ognuna
    for i in range(num_crops_x):
        for j in range(num_crops_y):
            # Calcola i punti di taglio
            left = i * crop_size
            upper = j * crop_size
            right = left + crop_size
            lower = upper + crop_size

            # Esegui il taglio dell'immagine
            cropped_image = image[upper:lower, left:right]

            # Genera il nome del file per l'immagine tagliata
            filename = f"{image_name}_{i}_{j}.jpg"

            # Salva l'immagine tagliata nel percorso di salvataggio
            save_filepath = os.path.join(save_path, filename)
            cv2.imwrite(save_filepath, cropped_image)

            # Visualizza il percorso di salvataggio dell'immagine
            # print(f"Immagine salvata: {save_filepath}")


In [5]:
path = 'data/uerd/'


for folder in ['cover/', 'stego/']:
    for image in os.listdir(path + folder):
        print(f"Cropping image {image}")
        crop_images(path + folder, image, f'data/cropped_uerd/{folder}', 128)
        print('-'*100)

Cropping image 000002.jpg
----------------------------------------------------------------------------------------------------
Cropping image 000004.jpg
----------------------------------------------------------------------------------------------------
Cropping image 000007.jpg
----------------------------------------------------------------------------------------------------
Cropping image 000012.jpg
----------------------------------------------------------------------------------------------------
Cropping image 000021.jpg
----------------------------------------------------------------------------------------------------
Cropping image 000023.jpg
----------------------------------------------------------------------------------------------------
Cropping image 000025.jpg
----------------------------------------------------------------------------------------------------
Cropping image 000029.jpg
-------------------------------------------------------------------------------------